# <center> Analyse de la concentration de CO2, <center>

In [ ]:
%matplotlib inline
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import datetime
from scipy import interpolate
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "last_expr"    
# ‘all’|’last’|’last_expr’|’none’
#https://jupyter-console.readthedocs.io/en/4.0.1/config_options.html
pd.options.display.max_rows = 10

Nous récupérons les données les plus récentes sur le site en pointant sur un fichier au format .csv, si cette récupération est possible nous enregistrons une copie de ce fichier. Si pour une raison quelconque nous n'arrivons pas a faire ce téléchargement, nous travaillons sur le dernières données téléchargé.

In [ ]:
try:
    raw_data = pd.read_csv("https://scrippsco2.ucsd.edu/assets/data/atmospheric/stations/"
                           "in_situ_co2/monthly/monthly_in_situ_co2_mlo.csv",skiprows=56)
except OSError as err:
    print("Erreur lors du téléchargement : {0}".format(err))
    print("Nous téléchargeons les dernières données enregistrer sur notre PC")
    raw_data = pd.read_csv("monthly_in_situ_co2_mlo")
except:
    print("Unexpected error:", sys.exc_info()[0])
    raise
else:
    raw_data.to_csv('monthly_in_situ_co2_mlo',index=True)

print(raw_data.shape)
raw_data

Nous voyons que les noms des colonnes ne sont pas très représentatives, nous modifions  les noms des colonnes

In [ ]:
raw_data_1 = raw_data.copy()
print(raw_data.columns)
raw_data_1.columns = ['Yr','Mn','Date 1','Date 2','s1','s2','s3','s4','s5','s6']

In [ ]:
raw_data_1.head()

Les données vide sont représentés par la valeur -99.99, nous remplaçons cette valeur par une valeur plus adéquate NaN dans une autre DataFrame

In [ ]:
date = datetime.date.today()
data = raw_data_1.copy()
data = data.drop(data[(data.Yr == date.year) & (data.Mn > date.month)].index)
data = data.replace(-99.99,np.NaN);
d = data[(data.Yr == date.year)].index
i,k = d[0], d[-1]

while k>=i:
    if data.loc[k].isnull().any():
        data = data.drop(k)
    else:
        break
    k = k - 1
    
annee, mois  = data.Yr[0], data.Mn[0]
d = data[(data.Yr == annee)].index
i,k = d[0], d[-1]

while i<=k:
    if data.loc[i].isnull().any():
        data = data.drop(i)
    else:
        break
    i = i + 1
InteractiveShell.ast_node_interactivity = "all"     
data.head(3)
data.tail(3)
InteractiveShell.ast_node_interactivity = "last_expr"  

On visualise les lignes dont une donnée colonne est manquante.

In [ ]:
data[data.isnull().any(axis=1)]

In [ ]:
data.head()

On ajoute un index 'périod' à la DataFrame, cet index représente la période de mesure. 
Cette date est mise dans au format compréhensible par pandas. On visualise toutes les lignes qui seront supprimées.

In [ ]:
df = data.dropna().copy()
df = df.reset_index().copy()
#print(data.shape)
period = [datetime.date(y,m,1) for y,m in zip(df['Yr'],df['Mn'])]
period = pd.Series(period,name = 'period')
#print(period.shape)
df = pd.concat([df,period],axis=1)
df = df.set_index('period') 
df.head()

Représentation graphique de la concentration  de CO2 de 1958 à nos jours

In [ ]:
df['s1'].plot(title = 'concentration de CO2',);
df['s1'].plot(figsize=(15, 10),).grid(linestyle='--', linewidth=1);

Nous allons approximé la concentration de CO2 avec une droite $a*x+b$, puis faire la différence pour 
n'obtenir que les variations de la concentration de CO2.

In [ ]:
from scipy import stats

a, b, r_value, p_value, std_err = stats.linregress(df['Date 2'], df['s1'])
def predict(x):
    return a*x+b

data_lineaire = df.copy()
data_lineaire['reg_lineaire'] = predict(data_lineaire['Date 2'])

fig = plt.figure(figsize=(18, 5))
ax1 = fig.add_subplot(121)
ax2 = fig.add_subplot(122)
ax1.grid(linestyle='--', linewidth=1)
ax2.grid(linestyle='--', linewidth=1)
#plot(figsize=(8, 5))  .plot(figsize=(15, 10), grid=True).grid(linestyle='--', linewidth=1);

ax1.set(title = 'Concentration CO2',xlabel='Période',ylabel='Concentration (ppm)')
ax1.plot(data_lineaire['s1'])
#data1['s1'].plot()
ax1.plot(data_lineaire['reg_lineaire']) 
data_lineaire['co2'] = data_lineaire['reg_lineaire']-data_lineaire['s1']
ax2.set(title = 'Variation de la concentration CO2',xlabel='Période',ylabel='Concentration (ppm)')
ax2.plot(data_lineaire['co2']); 

Le résultat n'est pas satisfaisant ...
Nous pouvons faire une optimisation avec une fonction de la forme $a*(x-b)^2+c$

In [ ]:
from scipy.optimize import curve_fit

def func_cube(x,a,b,c):
    return a*(x-b)**(2)+c

data_cube = df.copy()
popt, pcov = curve_fit(func_cube,data_cube['Date 2'],data_cube['s1'])

def fcube(x):
    return popt[0]*(x- popt[1])**(2)+popt[2]

data_cube['reg_cube'] = fcube(data_cube['Date 2'])

fig = plt.figure(figsize=(18, 5))
ax1 = fig.add_subplot(121)
ax2 = fig.add_subplot(122)
ax1.grid(linestyle='--', linewidth=1)
ax2.grid(linestyle='--', linewidth=1)

ax1.set(title = 'Concentration CO2',xlabel='Période',ylabel='Concentration (ppm)')
ax1.plot(data_cube['s1'])
ax1.plot(data_cube['reg_cube']) 
data_cube['co2'] = data_cube['reg_cube']-data_cube['s1']
ax2.set(title = 'Variation de la concentration CO2',xlabel='Période',ylabel='Concentration (ppm)')
ax2.plot(data_cube['co2']); 

Nous recherchons l'oscillation lente, pour cela nous allons opéré en 2 etapes :
- Recherche de la fréquence lente, par FFT. Pour cela nous devons faire une interpolation pour les quelque points manquant. Ce qui nous donnera une gamme de fréquence possible (échantillonne de la FFT)
- Pour la gamme de fréquence spécifiées, nous  estimons tous les paramètres pour une approximation sinusoïdale (moyenne, amplitude et phase) par les moindres carrés ordinaires 


In [ ]:
df = data.reset_index().copy()
df['period'] = pd.Series([datetime.date(y,m,1) for y,m in zip(df['Yr'],df['Mn'])])
df = df.set_index('period')   
df.head()
d = df[df.isnull().any(axis=1)]
d

In [ ]:
df.tail()

Pour les valeur manquantes, nous allons faire une interpolation linéaire afin que la FFT dispose de données prisent à échantillonnage de 1 mois.

In [ ]:
df = df.interpolate(method='linear', limit_direction='forward',limit=3)
df

In [ ]:
d = df[(df.Yr >= 1964) & (df.Yr < 1965)]
d

In [ ]:
data_cube = df.copy()
popt, pcov = curve_fit(func_cube,data_cube['Date 2'],data_cube['s1'])
data_cube['reg_cube'] = fcube(data_cube['Date 2'])
data_cube['co2'] = data_cube['reg_cube']-data_cube['s1']

nb = len(data_cube['Date 2'])
ecart = []
for i in np.arange(0,nb-1):
    ecart.append(data_cube['Date 2'][i+1] - data_cube['Date 2'][i])
dt = np.mean(ecart)
dt

Utilisation de la fonction np.fft.fft pour transformer le signal temporel en signal fréquentiel à l’aide de la transformée de Fourier rapide. Le résultat s1_fft est un tableau de nombres complexes. La densité spectrale de puissance est calculée à l’aide de la formule Γx=|X|2T. Les fréquences sont ensuite calculées à l’aide de la fonction np.fft.fftfreq.

In [ ]:
s1 = data_cube.co2 - data_cube.co2.mean()

# calcul de la transformee de Fourier et des frequences
s1_fft = np.fft.fft(s1)

n = s1.size
dt = 1/12
pds_s1 = (dt/n) * np.abs(s1_fft)**2  # densité spectral de puissance
freq = np.fft.fftfreq(n, d=dt)       # fréquences associées

freq = freq[:n/2]
pds_s1 = pds_s1[:n/2]
# affichage de la transformee de Fourier
plt.figure(figsize=(18, 10))
plt.stem(freq, pds_s1, label="PSD")


Finalement, seules les « moitiés droites » des tableaux sont conservées car les gauches contiennent les fréquences négatives. Ces opérations sont réalisées àl’aide duslicingpython (tranchage)

In [ ]:
plt.stem(freq[0:100], abs(s1_fft.real[0:100]), label="real")

In [ ]:
type(s1_fft.real)
N = (len(s1_fft.real)+1)/2
N = int(N)
indide_f = np.where(s1_fft.real[0:N] > 500)
f_lente = indide_f[0][0] * (1/dt)

f_rapide = indide_f[0][-1] * (1/dt)
print(f' Estimation de la frequence lente : {f_lente} \n Esitmation de la fréquence rapide : {f_rapide}')
